# Iteración inicial de modelos predictivos

In [1]:
import pandas as pd
import numpy as np

import missingno as msno
import matplotlib.pyplot as plt
import plotly.express as px

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split 
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.decomposition import TruncatedSVD

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
import datetime
from dateutil.parser import parse
from sklearn.tree import  DecisionTreeClassifier
import plotly.graph_objects as go
import umap
from imblearn.under_sampling import RandomUnderSampler
from imblearn.over_sampling import RandomOverSampler

In [2]:
# Seteo jupyter notebook
pd.set_option('display.max_columns', None)

In [3]:
Data=pd.read_csv("consolidation_30May2022.csv").drop(columns=["Unnamed: 0"]).fillna("")
Data.head()

c:\Users\Jose Luis\anaconda3\envs\Programacion_Cientifica\lib\site-packages\IPython\core\interactiveshell.py:3441: DtypeWarning: Columns (40) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


pref_B-B  pref_D-E  pref_C-D  pref_A-A  Duracion_Campaña    B    C  \
0       0.0       0.0       0.0       0.0               1.0  4.0  5.0   
1       0.0       0.0       0.0       0.0               1.0  6.0  6.0   
2       0.0       0.0       0.0       0.0               1.0  2.0  3.0   
3       0.0       0.0       0.0       0.0               1.2  7.0  3.0   
4       0.0       0.0       0.0       0.0               1.0  4.0  1.0   

   lec_B-B  lec_E-E  lec_D-E  lec_C-D  lec_A-A  num_comunicaciones  Length  \
0      5.0      0.0      0.0      0.0      0.0                22.0     371   
1      8.0      0.0      1.0      1.0      0.0                15.0     371   
2      1.0      0.0      0.0      1.0      0.0                26.0     371   
3      5.0      0.0      0.0      2.0      2.0                34.0     371   
4      1.0      0.0      0.0      0.0      0.0                24.0     371   

           Monto  Frequency  Periodicity     Recency  F-D  F-H  F-I  F-J  G-K  \
0  180754.821871        396         91.0  652.012626   17   19    2   19   47   
1  154439.534968        416        102.0  649.634615    2   17   16   17  266   
2  128719.371341        395        107.0  629.587342    2   15   13   17  272   
3  142752.939212        698         69.0  690.118911   15    0    0   19  144   
4  127120.640500        374        112.0  613.438503    0   19    0   19  284   

   A-G  A-K  C-C  D-F  E-F  A-L  Positivo  Negativo  Sin Info        Edad  \
0   18  274    0    0    0    0        36       342        18  Mayor a 70   
1   16   69    0    2    3    0        23       377        16  Mayor a 70   
2   20   51    0    2    0    0        22       353        20  Mayor a 70   
3   20  465    0    0   15    6        54       624        20  Mayor a 70   
4   17   27    0    3    1    0        23       334        17  Mayor a 70   

   Sexo Renta  Recibe_sueldo_en_cuenta Segmento_consumidor Meses_antiguedad  \
0     1    R1                        0                   A  Mayor a 10 años   
1     1    R4                        0                   A  Mayor a 10 años   
2     1    R5                        0                   A  Mayor a 10 años   
3     1    R9                        0                   A  Mayor a 10 años   
4     0    R2                        0                   B  Mayor a 10 años   

  Comuna Ciudad Estado_civil Principalidad Profesion       Target  
0  331.0   13.0            D             B      P164               
1   91.0   13.0            D             B       P85  E-E B-B D-E  
2   34.0    5.0            B             C      P143      D-E A-A  
3  331.0   13.0            B             C        P1          E-E  
4   37.0    5.0            D             F      P210          D-E

In [4]:
# datos númericos
numerical=list(Data.select_dtypes(exclude=["category","object"]).columns)
numerical.remove("Sexo")
numerical.remove('Recibe_sueldo_en_cuenta')


# datos categorical
categorical=list(Data.select_dtypes(include=["category","object"]).columns)+['Sexo','Recibe_sueldo_en_cuenta']
categorical.remove("Target")

In [5]:
for i in categorical:
    Data[i]=Data[i].astype(str)

In [7]:
X=Data[numerical+categorical]
X.head()

pref_B-B  pref_D-E  pref_C-D  pref_A-A  Duracion_Campaña    B    C  \
0       0.0       0.0       0.0       0.0               1.0  4.0  5.0   
1       0.0       0.0       0.0       0.0               1.0  6.0  6.0   
2       0.0       0.0       0.0       0.0               1.0  2.0  3.0   
3       0.0       0.0       0.0       0.0               1.2  7.0  3.0   
4       0.0       0.0       0.0       0.0               1.0  4.0  1.0   

   lec_B-B  lec_E-E  lec_D-E  lec_C-D  lec_A-A  num_comunicaciones  Length  \
0      5.0      0.0      0.0      0.0      0.0                22.0     371   
1      8.0      0.0      1.0      1.0      0.0                15.0     371   
2      1.0      0.0      0.0      1.0      0.0                26.0     371   
3      5.0      0.0      0.0      2.0      2.0                34.0     371   
4      1.0      0.0      0.0      0.0      0.0                24.0     371   

           Monto  Frequency  Periodicity     Recency  F-D  F-H  F-I  F-J  G-K  \
0  180754.821871        396         91.0  652.012626   17   19    2   19   47   
1  154439.534968        416        102.0  649.634615    2   17   16   17  266   
2  128719.371341        395        107.0  629.587342    2   15   13   17  272   
3  142752.939212        698         69.0  690.118911   15    0    0   19  144   
4  127120.640500        374        112.0  613.438503    0   19    0   19  284   

   A-G  A-K  C-C  D-F  E-F  A-L  Positivo  Negativo  Sin Info        Edad  \
0   18  274    0    0    0    0        36       342        18  Mayor a 70   
1   16   69    0    2    3    0        23       377        16  Mayor a 70   
2   20   51    0    2    0    0        22       353        20  Mayor a 70   
3   20  465    0    0   15    6        54       624        20  Mayor a 70   
4   17   27    0    3    1    0        23       334        17  Mayor a 70   

  Renta Segmento_consumidor Meses_antiguedad Comuna Ciudad Estado_civil  \
0    R1                   A  Mayor a 10 años  331.0   13.0            D   
1    R4                   A  Mayor a 10 años   91.0   13.0            D   
2    R5                   A  Mayor a 10 años   34.0    5.0            B   
3    R9                   A  Mayor a 10 años  331.0   13.0            B   
4    R2                   B  Mayor a 10 años   37.0    5.0            D   

  Principalidad Profesion Sexo Recibe_sueldo_en_cuenta  
0             B      P164    1                       0  
1             B       P85    1                       0  
2             C      P143    1                       0  
3             C        P1    1                       0  
4             F      P210    0                       0

In [8]:
Y=Data["Target"]
Y.head()

0               
1    E-E B-B D-E
2        D-E A-A
3            E-E
4            D-E
Name: Target, dtype: object

In [41]:
# Generación de conjuntos de train y test
Xtrain, Xtest, Ytrain, Ytest = train_test_split(
    X, Y, test_size=0.33, 
    shuffle=True,
    
) 

In [10]:
# RUS (ELimina aleatorias clases mayoritaria):
rus=RandomUnderSampler(random_state=0) # Random_state=0

In [42]:
# Sobremuestreo: Aumentar numero de datos de la clase minoritaria
# ROS(Duplica clases):
ros=RandomOverSampler(random_state=0) # Random_state=0

In [43]:
# ROS:
Xtrain, Ytrain=ros.fit_resample(Xtrain,Ytrain)

In [44]:
# Visualización
px.histogram(Ytrain, x="Target",title="Distribution Plot Target")

**Todas las variables**

In [13]:
preprocessing_transformer = ColumnTransformer(
    transformers=[('OneHotEncoder', OneHotEncoder(handle_unknown="ignore"), categorical),
        ('MinMax', MinMaxScaler(),numerical),
    ])

In [14]:
pipe = Pipeline(
    [("preprocesamiento", preprocessing_transformer),
     #("Selection", SelectPercentile(f_classif, percentile=80)),
     #("red_atributos",TruncatedSVD(n_components=300)),
     ("clf",RandomForestClassifier(random_state=1))]
)


In [56]:
RandomForestClassifier(random_state=1).get_params()

{'bootstrap': True,
 'ccp_alpha': 0.0,
 'class_weight': None,
 'criterion': 'gini',
 'max_depth': None,
 'max_features': 'auto',
 'max_leaf_nodes': None,
 'max_samples': None,
 'min_impurity_decrease': 0.0,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 100,
 'n_jobs': None,
 'oob_score': False,
 'random_state': 1,
 'verbose': 0,
 'warm_start': False}

In [15]:
# Entrenamiento de pipelines
pipe.fit(Xtrain, Ytrain)


Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('OneHotEncoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['Edad', 'Renta',
                                                   'Segmento_consumidor',
                                                   'Meses_antiguedad', 'Comuna',
                                                   'Ciudad', 'Estado_civil',
                                                   'Principalidad', 'Profesion',
                                                   'Sexo',
                                                   'Recibe_sueldo_en_cuenta']),
                                                 ('MinMax', MinMaxScaler(),
                                                  ['pref_B-B', 'pref_D-E',
                                                   'pref_C-D', 'pref_A-A',
                                                   'Duracion

In [16]:
# Generación de predicciones
Ypred = pipe.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

              precision    recall  f1-score   support

                   0.48      0.72      0.57      2762
         A-A       0.40      0.16      0.23      1195
     A-A B-B       0.46      0.06      0.11      1299
     A-A D-E       0.14      0.04      0.06       746
         B-B       0.26      0.33      0.29      1203
     B-B C-D       0.43      0.17      0.24       503
     B-B D-E       0.17      0.22      0.19       802
 B-B D-E E-E       0.08      0.03      0.05       498
     B-B E-E       0.28      0.13      0.18       800
 B-B E-E D-E       0.14      0.08      0.10       370
         C-D       0.44      0.68      0.53       688
     C-D B-B       0.48      0.37      0.42       578
 C-D B-B D-E       0.28      0.27      0.28       302
     C-D D-E       0.24      0.43      0.31       295
 C-D D-E B-B       0.18      0.20      0.19       283
     C-D E-E       0.52      0.50      0.51       449
 C-D E-E D-E       0.51      0.39      0.44       222
         D-E       0.21    

**Criterio CorrKill**

In [17]:
tags1=['E-F',
 'C-C',
 'D-F',
 'A-K',
 'num_comunicaciones',
 'Length',
 'pref_A-A',
 'Positivo',
 'Recency',
 'A-G',
 'Monto',
 'Periodicity',
 'Frequency',
 'lec_B-B',
 'G-K',
 'Profesion',
 'lec_C-D',
 'F-H',
 'F-I',
 'Renta',
 'B',
 'Edad',
 'Comuna',
 'Sin Info',
 'A-L',
 'F-D',
 'Principalidad',
 'F-J',
 'Duracion_Campaña']

In [18]:
numerical1=list(filter(lambda x:x  in numerical,tags1))
categorical1=list(filter(lambda x:x  in categorical,tags1))

In [19]:
preprocessing_transformer1 = ColumnTransformer(
    transformers=[('OneHotEncoder', OneHotEncoder(handle_unknown="ignore"), categorical1),
        ('MinMax', MinMaxScaler(),numerical1),
    ])

In [20]:
pipe1 = Pipeline(
    [("preprocesamiento", preprocessing_transformer1),
     #("Selection", SelectPercentile(f_classif, percentile=80)),
     #("red_atributos",TruncatedSVD(n_components=300)),
     ("clf",RandomForestClassifier(random_state=1))]
)

In [21]:
# Entrenamiento de pipelines
pipe1.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('OneHotEncoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['Profesion', 'Renta', 'Edad',
                                                   'Comuna', 'Principalidad']),
                                                 ('MinMax', MinMaxScaler(),
                                                  ['E-F', 'C-C', 'D-F', 'A-K',
                                                   'num_comunicaciones',
                                                   'Length', 'pref_A-A',
                                                   'Positivo', 'Recency', 'A-G',
                                                   'Monto', 'Periodicity',
                                                   'Frequency', 'lec_B-B',
                                                   'G-K', 'lec_C-D', 'F-H',
                                     

In [22]:
# Generación de predicciones
Ypred = pipe1.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

              precision    recall  f1-score   support

                   0.47      0.72      0.57      2695
         A-A       0.45      0.17      0.25      1220
     A-A B-B       0.52      0.07      0.12      1400
     A-A D-E       0.17      0.04      0.07       793
         B-B       0.24      0.32      0.28      1131
     B-B C-D       0.45      0.16      0.24       540
     B-B D-E       0.18      0.22      0.20       836
 B-B D-E E-E       0.12      0.05      0.07       466
     B-B E-E       0.31      0.15      0.20       826
 B-B E-E D-E       0.13      0.07      0.09       389
         C-D       0.43      0.68      0.53       669
     C-D B-B       0.50      0.37      0.43       582
 C-D B-B D-E       0.22      0.25      0.24       261
     C-D D-E       0.25      0.43      0.32       300
 C-D D-E B-B       0.20      0.23      0.21       275
     C-D E-E       0.56      0.51      0.53       466
 C-D E-E D-E       0.55      0.41      0.47       228
         D-E       0.23    

**Principales criterio Información Gini**

In [45]:
tags2=['E-F',
 'C-C',
 'D-F',
 'A-K',
 'num_comunicaciones',
 'Length',
 'pref_A-A',
 'Positivo',
 'Recency',
 'A-G',
 'Monto',
 'Periodicity',
 'Frequency',
 'lec_B-B',
 'G-K']

In [46]:
numerical2=list(filter(lambda x:x  in numerical,tags2))
categorical2=list(filter(lambda x:x  in categorical,tags2))

In [53]:
numerical2

['E-F',
 'C-C',
 'D-F',
 'A-K',
 'num_comunicaciones',
 'Length',
 'pref_A-A',
 'Positivo',
 'Recency',
 'A-G',
 'Monto',
 'Periodicity',
 'Frequency',
 'lec_B-B',
 'G-K']

In [54]:
categorical2

[]

In [47]:
preprocessing_transformer2 = ColumnTransformer(
    transformers=[('OneHotEncoder', OneHotEncoder(handle_unknown="ignore"), categorical2),
        ('MinMax', MinMaxScaler(),numerical2),
    ])

In [48]:
pipe2 = Pipeline(
    [("preprocesamiento", preprocessing_transformer2),
     #("Selection", SelectPercentile(f_classif, percentile=80)),
     #("red_atributos",TruncatedSVD(n_components=300)),
     ("clf",RandomForestClassifier(random_state=1))]
)

In [49]:
# Entrenamiento de pipelines
pipe2.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('OneHotEncoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  []),
                                                 ('MinMax', MinMaxScaler(),
                                                  ['E-F', 'C-C', 'D-F', 'A-K',
                                                   'num_comunicaciones',
                                                   'Length', 'pref_A-A',
                                                   'Positivo', 'Recency', 'A-G',
                                                   'Monto', 'Periodicity',
                                                   'Frequency', 'lec_B-B',
                                                   'G-K'])])),
                ('clf', RandomForestClassifier(random_state=1))])

In [28]:
# Generación de predicciones
Ypred = pipe2.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

              precision    recall  f1-score   support

                   0.50      0.74      0.59      2793
         A-A       0.39      0.16      0.23      1128
     A-A B-B       0.47      0.06      0.11      1340
     A-A D-E       0.17      0.04      0.06       887
         B-B       0.28      0.34      0.31      1253
     B-B C-D       0.44      0.20      0.28       419
     B-B D-E       0.18      0.24      0.20       773
 B-B D-E E-E       0.09      0.05      0.06       406
     B-B E-E       0.34      0.16      0.22       832
 B-B E-E D-E       0.17      0.09      0.12       401
         C-D       0.49      0.71      0.58       734
     C-D B-B       0.53      0.40      0.46       590
 C-D B-B D-E       0.25      0.28      0.26       267
     C-D D-E       0.28      0.45      0.35       332
 C-D D-E B-B       0.21      0.24      0.22       272
     C-D E-E       0.51      0.61      0.56       357
 C-D E-E D-E       0.54      0.49      0.52       189
         D-E       0.23    

In [50]:
# Generación de predicciones
Ypred = pipe2.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

              precision    recall  f1-score   support

                   0.79      0.65      0.71      4873
         A-A       0.27      0.51      0.35       253
     A-A B-B       0.04      0.17      0.07        46
     A-A D-E       0.00      0.00      0.00        12
         B-B       0.53      0.41      0.46      2003
     B-B C-D       0.14      0.29      0.19       107
     B-B D-E       0.16      0.24      0.19       704
 B-B D-E E-E       0.02      0.08      0.03        60
     B-B E-E       0.08      0.21      0.12       140
 B-B E-E D-E       0.05      0.11      0.07       107
         C-D       0.76      0.60      0.67      1300
     C-D B-B       0.45      0.41      0.43       485
 C-D B-B D-E       0.24      0.35      0.29       215
     C-D D-E       0.50      0.40      0.45       614
 C-D D-E B-B       0.16      0.20      0.18       259
     C-D E-E       0.58      0.64      0.61       390
 C-D E-E D-E       0.55      0.64      0.59       165
         D-E       0.54    

**Criterio solo Top correlación**

In [35]:
tags3=['C-C', 'Positivo', 'Frequency', 'num_comunicaciones', 'Recency',
       'lec_C-D', 'Negativo', 'F-J', 'B', 'D-F', 'A-K', 'Length', 'Sin Info',
       'A-G', 'E-F', 'Principalidad', 'C', 'lec_B-B', 'F-I', 'F-H', 'pref_C-D',
       'Ciudad', 'Segmento_consumidor', 'F-D', 'Duracion_Campaña']

In [36]:
numerical3=list(filter(lambda x:x  in numerical,tags3))
categorical3=list(filter(lambda x:x  in categorical,tags3))

In [37]:
preprocessing_transformer3 = ColumnTransformer(
    transformers=[('OneHotEncoder', OneHotEncoder(handle_unknown="ignore"), categorical3),
        ('MinMax', MinMaxScaler(),numerical3),
    ])

In [38]:
pipe3 = Pipeline(
    [("preprocesamiento", preprocessing_transformer3),
     #("Selection", SelectPercentile(f_classif, percentile=80)),
     #("red_atributos",TruncatedSVD(n_components=300)),
     ("clf",RandomForestClassifier(random_state=1))]
)

In [39]:
# Entrenamiento de pipelines
pipe3.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('OneHotEncoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['Principalidad', 'Ciudad',
                                                   'Segmento_consumidor']),
                                                 ('MinMax', MinMaxScaler(),
                                                  ['C-C', 'Positivo',
                                                   'Frequency',
                                                   'num_comunicaciones',
                                                   'Recency', 'lec_C-D',
                                                   'Negativo', 'F-J', 'B',
                                                   'D-F', 'A-K', 'Length',
                                                   'Sin Info', 'A-G', 'E-F',
                                                   'C', 'lec_B-B', 'F

In [40]:
# Generación de predicciones
Ypred = pipe3.predict(Xtest)
# Métricas de evaluación 
print(classification_report(Ypred, Ytest))

              precision    recall  f1-score   support

                   0.44      0.73      0.54      2478
         A-A       0.37      0.12      0.18      1510
     A-A B-B       0.50      0.07      0.12      1365
     A-A D-E       0.16      0.04      0.06       852
         B-B       0.26      0.36      0.30      1118
     B-B C-D       0.47      0.19      0.27       478
     B-B D-E       0.18      0.24      0.20       764
 B-B D-E E-E       0.08      0.04      0.06       408
     B-B E-E       0.36      0.16      0.22       890
 B-B E-E D-E       0.14      0.07      0.10       401
         C-D       0.48      0.70      0.57       720
     C-D B-B       0.51      0.39      0.44       576
 C-D B-B D-E       0.28      0.29      0.28       276
     C-D D-E       0.29      0.46      0.36       329
 C-D D-E B-B       0.18      0.21      0.20       272
     C-D E-E       0.53      0.58      0.55       394
 C-D E-E D-E       0.54      0.46      0.50       203
         D-E       0.19    